First, I initiate my connection to Spotify API.

In [1]:
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials

sp = spotipy.Spotify(auth_manager=SpotifyClientCredentials(client_id="1bc14e5e30a44160b7190a4c449b7f8d",
                                                           client_secret="d92e328d86684bc6a23b2d3534353b45"))

Second, I get the tracks for one of my huge playlists.

In [2]:
def get_playlist_tracks(username, playlist_id):
    results = sp.playlist_tracks(playlist_id)
    tracks = results['items']

    while results['next']:
        results = sp.next(results)
        tracks.extend(results['items'])

    return tracks

In [3]:
tracks = get_playlist_tracks('1119739647', '1UUPBq4KjOS6X7mDEVRvPt')

I check how many songs I have.

In [4]:
print(len(tracks))

3290


The file is too big to print, so I convert it to JSON to examine it.

In [5]:
import json

with open('tracks.json', 'w') as f:
    json.dump(tracks, f, indent=4)

In [6]:
tracks

[{'added_at': '2016-01-01T17:45:10Z',
  'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/1119739647'},
   'href': 'https://api.spotify.com/v1/users/1119739647',
   'id': '1119739647',
   'type': 'user',
   'uri': 'spotify:user:1119739647'},
  'is_local': False,
  'primary_color': None,
  'track': {'album': {'album_type': 'single',
    'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/2JKC6GoQgJGCaGLwAcmBaH'},
      'href': 'https://api.spotify.com/v1/artists/2JKC6GoQgJGCaGLwAcmBaH',
      'id': '2JKC6GoQgJGCaGLwAcmBaH',
      'name': 'Venom Is Bliss',
      'type': 'artist',
      'uri': 'spotify:artist:2JKC6GoQgJGCaGLwAcmBaH'}],
    'available_markets': ['AD',
     'AE',
     'AG',
     'AL',
     'AM',
     'AO',
     'AR',
     'AT',
     'AU',
     'AZ',
     'BA',
     'BB',
     'BD',
     'BE',
     'BF',
     'BG',
     'BH',
     'BI',
     'BJ',
     'BN',
     'BO',
     'BR',
     'BS',
     'BT',
     'BW',
     'BY',
     '

I now create lists to store the names of the song, artists and their respective ids.

In [7]:
import pandas as pd

song_names = []
artist_names = []
song_ids = []
artist_ids = []

for track in tracks:
    if track['track'] is None:
        continue
    
    song_names.append(track['track']['name'])
    song_ids.append(track['track']['id'])
    
    artist_names.append(track['track']['artists'][0]['name'])
    artist_ids.append(track['track']['artists'][0]['id'])

I create a dataframe with those lists.

In [8]:
data = {
    'song_name': song_names,
    'artist_name': artist_names,
    'song_id': song_ids,
    'artist_id': artist_ids
}

In [9]:
df = pd.DataFrame(data)
df

song_name         artist_name                 song_id  \
0                    One Week      Venom Is Bliss  1Ykhi4Cz7KFodDB9goiurk   
1                       Roses    The Chainsmokers  3vv9phIu6Y1vX3jcqaGz5Z   
2                        Warm            SG Lewis  1BgSJnoM44sIin6ESsZMkP   
3     This Stage Is Your Life       A Silent Film  1TUShkMcJFI32SwpMWWN9l   
4                    I'm Good        The Mowgli's  0YsX1Thbt24s1XP68RMTHM   
...                       ...                 ...                     ...   
3284                 Comedown              Joesef  2EjgVZre5ONvZLNw59kEIn   
3285             Sogni di R&R             Ligabue  6VdEQljDsj3gqY33FDqlLS   
3286       Through The Echoes        Paolo Nutini  13KhcUWu9WucFw0h5jB88R   
3287                A Semente    Bezerra Da Silva  7mKFzy9cFV6fbIIVD3rSp9   
3288                    Angie  The Rolling Stones  1GcVa4jFySlun4jLSuMhiq   

                   artist_id  
0     2JKC6GoQgJGCaGLwAcmBaH  
1     69GGBxA162lTqCwzJG5jLp  
2     0GG2cWaonE4JPrjcCCQ1EG  
3     7HO5HS3yeokRBGVC4nSKIb  
4     6AGUQK1EWK6nvN4pLIDQDQ  
...                      ...  
3284  28EyduqESEOVMO6vglvaUZ  
3285  7H8ZC8uHJMPZGLMApRRNIz  
3286  7x5rK9BClDQ8wmCkYAGsQp  
3287  3aqtJPuhfwxQ60jG1OAFQt  
3288  22bE4uQ6baNwSHPVcDxLCe  

[3289 rows x 4 columns]

I got the audio features from https://developer.spotify.com/documentation/web-api/reference/get-audio-features, request them for each song id, store them in a list and then added them to my dataframe.

In [10]:
danceability = []
energy = []
key = []
loudness = []
mode = []
speechiness = []
acousticness = []
instrumentalness = []
liveness = []
valence = []
tempo = []

for song_id in df['song_id']:
    audio_features = sp.audio_features(song_id)[0] 
    danceability.append(audio_features['danceability'])
    energy.append(audio_features['energy'])
    key.append(audio_features['key'])
    loudness.append(audio_features['loudness'])
    mode.append(audio_features['mode'])
    speechiness.append(audio_features['speechiness'])
    acousticness.append(audio_features['acousticness'])
    instrumentalness.append(audio_features['instrumentalness'])
    liveness.append(audio_features['liveness'])
    valence.append(audio_features['valence'])
    tempo.append(audio_features['tempo'])

df['danceability'] = danceability
df['energy'] = energy
df['key'] = key
df['loudness'] = loudness
df['mode'] = mode
df['speechiness'] = speechiness
df['acousticness'] = acousticness
df['instrumentalness'] = instrumentalness
df['liveness'] = liveness
df['valence'] = valence
df['tempo'] = tempo

df

song_name         artist_name                 song_id  \
0                    One Week      Venom Is Bliss  1Ykhi4Cz7KFodDB9goiurk   
1                       Roses    The Chainsmokers  3vv9phIu6Y1vX3jcqaGz5Z   
2                        Warm            SG Lewis  1BgSJnoM44sIin6ESsZMkP   
3     This Stage Is Your Life       A Silent Film  1TUShkMcJFI32SwpMWWN9l   
4                    I'm Good        The Mowgli's  0YsX1Thbt24s1XP68RMTHM   
...                       ...                 ...                     ...   
3284                 Comedown              Joesef  2EjgVZre5ONvZLNw59kEIn   
3285             Sogni di R&R             Ligabue  6VdEQljDsj3gqY33FDqlLS   
3286       Through The Echoes        Paolo Nutini  13KhcUWu9WucFw0h5jB88R   
3287                A Semente    Bezerra Da Silva  7mKFzy9cFV6fbIIVD3rSp9   
3288                    Angie  The Rolling Stones  1GcVa4jFySlun4jLSuMhiq   

                   artist_id  danceability  energy  key  loudness  mode  \
0     2JKC6GoQgJGCaGLwAcmBaH         0.537   0.669    5    -5.797     1   
1     69GGBxA162lTqCwzJG5jLp         0.713   0.802    4    -7.055     1   
2     0GG2cWaonE4JPrjcCCQ1EG         0.466   0.460   11   -13.928     0   
3     7HO5HS3yeokRBGVC4nSKIb         0.492   0.863    4    -5.129     0   
4     6AGUQK1EWK6nvN4pLIDQDQ         0.616   0.927    9    -5.235     0   
...                      ...           ...     ...  ...       ...   ...   
3284  28EyduqESEOVMO6vglvaUZ         0.451   0.268    9    -9.832     1   
3285  7H8ZC8uHJMPZGLMApRRNIz         0.507   0.605    7    -4.666     1   
3286  7x5rK9BClDQ8wmCkYAGsQp         0.730   0.487    7    -7.679     1   
3287  3aqtJPuhfwxQ60jG1OAFQt         0.670   0.557    2   -11.252     1   
3288  22bE4uQ6baNwSHPVcDxLCe         0.429   0.554    9    -6.128     0   

      speechiness  acousticness  instrumentalness  liveness  valence    tempo  
0          0.0337      0.115000          0.000001    0.1380    0.293  123.891  
1          0.0561      0.043500          0.003770    0.3090    0.343  100.001  
2          0.0849      0.518000          0.393000    0.1030    0.234   96.948  
3          0.0371      0.000555          0.038700    0.0863    0.479  134.991  
4          0.0706      0.008660          0.000000    0.1550    0.619   96.033  
...           ...           ...               ...       ...      ...      ...  
3284       0.0294      0.831000          0.000066    0.0830    0.206   89.513  
3285       0.0333      0.614000          0.000000    0.1090    0.432  171.657  
3286       0.0399      0.285000          0.000035    0.1350    0.314  104.933  
3287       0.1590      0.413000          0.000000    0.0888    0.875  100.933  
3288       0.0291      0.670000          0.000152    0.1050    0.407  136.302  

[3289 rows x 15 columns]